# Qualicum Beach Orthomosaic Processing with GCPs

This notebook processes drone imagery to create orthomosaics using Agisoft Metashape, comparing results with and without ground control points (GCPs).

## Workflow:
1. Load GCPs from KMZ file
2. Download drone imagery from S3 (all 12 cells)
3. Process orthomosaic WITHOUT GCPs
4. Process orthomosaic WITH GCPs
5. Compare both orthomosaics against ESRI and OpenStreetMap basemaps
6. Generate comprehensive quality report


## Setup and Imports


In [1]:
import sys
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt
import warnings
import logging
warnings.filterwarnings('ignore')

# Configure logging
logging.basicConfig(
    level=logging.INFO,
    format="%(asctime)s - %(name)s - %(levelname)s - %(message)s"
)

# Add package to path
package_dir = Path.cwd()
sys.path.insert(0, str(package_dir))

from qualicum_beach_gcp_analysis import (
    load_gcps_from_kmz,
    download_basemap,
    visualize_gcps_on_basemap,
    calculate_gcp_bbox,
    download_all_images_from_input_dir,
    export_to_metashape_csv,
    export_to_metashape_xml,
    process_orthomosaic,
    PhotoMatchQuality,
    DepthMapQuality,
    compare_orthomosaic_to_basemap,
    generate_comparison_report,
    generate_markdown_report,
)

print("✓ Imports successful!")


✓ Imports successful!


## Step 1: Load Ground Control Points


In [2]:
# Path to the KMZ file
kmz_path = "/Users/mauriciohessflores/Documents/Code/Data/Qualicum Beach GCPs/Spexi_Survey_Points/Spexi_Drone_Survey/QualicumBeach_AOI.kmz"

# Load GCPs
gcps = load_gcps_from_kmz(kmz_path)

print(f"\n✓ Loaded {len(gcps)} ground control points")

# Display all GCPs
if gcps:
    print("\nGCPs:")
    for i, gcp in enumerate(gcps):
        print(f"  {i+1:2d}. {gcp.get('id', 'Unknown'):20s}: ({gcp['lat']:.6f}, {gcp['lon']:.6f}, z={gcp.get('z', 0):.2f})")
else:
    print("\n⚠️  No GCPs found!")


Loading GCPs from: /Users/mauriciohessflores/Documents/Code/Data/Qualicum Beach GCPs/Spexi_Survey_Points/Spexi_Drone_Survey/QualicumBeach_AOI.kmz
Found 1 KML file(s) in KMZ
Attempting to fix namespace issues...
✓ Fixed namespace issues in KML file
Found 12 placemarks in KMZ file (namespace: http://www.opengis.net/kml/2.2)
Successfully parsed 12 GCPs from KMZ file

✓ Loaded 12 ground control points

GCPs:
   1. 8928d89ac03ffff     : (49.352544, -124.407904, z=0.00)
   2. 8928d89ac0bffff     : (49.354342, -124.404136, z=0.00)
   3. 8928d89ac1bffff     : (49.351585, -124.403857, z=0.00)
   4. 8928d89ac43ffff     : (49.355182, -124.396319, z=0.00)
   5. 8928d89ac47ffff     : (49.356141, -124.400367, z=0.00)
   6. 8928d89ac53ffff     : (49.352425, -124.396040, z=0.00)
   7. 8928d89ac57ffff     : (49.353384, -124.400088, z=0.00)
   8. 8928d89ac5bffff     : (49.354224, -124.392271, z=0.00)
   9. 8928d89ac73ffff     : (49.357100, -124.404415, z=0.00)
  10. 8928d89acc7ffff     : (49.348828, -12

## Step 2: Calculate Bounding Box and Download Reference Basemaps


In [3]:
# Create output directory
output_dir = Path("outputs")
output_dir.mkdir(exist_ok=True)

# Calculate bounding box
bbox = calculate_gcp_bbox(gcps, padding=0.01)
min_lat, min_lon, max_lat, max_lon = bbox

print(f"Bounding box:")
print(f"  Latitude: {min_lat:.6f} to {max_lat:.6f}")
print(f"  Longitude: {min_lon:.6f} to {max_lon:.6f}")

# Download ESRI World Imagery basemap (for comparison)
basemap_esri_path = str(output_dir / "qualicum_beach_basemap_esri.tif")
print("\nDownloading ESRI World Imagery basemap...")
basemap_esri_path = download_basemap(
    bbox=bbox,
    output_path=basemap_esri_path,
    source="esri_world_imagery",
    zoom=None
)
print(f"✓ ESRI basemap saved to: {basemap_esri_path}")

# Download OpenStreetMap basemap (for comparison)
basemap_osm_path = str(output_dir / "qualicum_beach_basemap_osm.tif")
print("\nDownloading OpenStreetMap basemap...")
basemap_osm_path = download_basemap(
    bbox=bbox,
    output_path=basemap_osm_path,
    source="openstreetmap",
    zoom=None
)
print(f"✓ OpenStreetMap basemap saved to: {basemap_osm_path}")


Bounding box:
  Latitude: 49.338828 to 49.367100
  Longitude: -124.417904 to -124.382271

Tile range: X [1264, 1265], Y [2800, 2801]
Basemap saved to outputs/qualicum_beach_basemap_esri.tif
✓ ESRI basemap saved to: outputs/qualicum_beach_basemap_esri.tif

Tile range: X [1264, 1265], Y [2800, 2801]
Basemap saved to outputs/qualicum_beach_basemap_osm.tif
✓ OpenStreetMap basemap saved to: outputs/qualicum_beach_basemap_osm.tif


## Step 3: Download Drone Imagery from S3


In [4]:
# Setup paths
input_dir = Path("input")
photos_dir = Path("input/images")

# Download all images from input manifest files
print("Downloading images from S3...")
print("=" * 60)
download_stats = download_all_images_from_input_dir(
    input_dir=input_dir,
    photos_dir=photos_dir,
    skip_existing=True  # Don't re-download if images already exist
)
print("=" * 60)
print("✓ Image download complete")


2025-12-02 12:16:07,176 - qualicum_beach_gcp_analysis.s3_downloader - INFO - Found 12 manifest files


2025-12-02 12:16:07,375 - qualicum_beach_gcp_analysis.s3_downloader - INFO - Processing manifest: input-file_172543.txt
2025-12-02 12:16:07,376 - qualicum_beach_gcp_analysis.s3_downloader - INFO -   Bucket: spexi-data-domain-assets-production-ca-central-1
2025-12-02 12:16:07,376 - qualicum_beach_gcp_analysis.s3_downloader - INFO -   S3 prefix: standardized-images/8928d89ac53ffff/172543/
2025-12-02 12:16:07,376 - qualicum_beach_gcp_analysis.s3_downloader - INFO -   Total images: 152
2025-12-02 12:16:07,379 - qualicum_beach_gcp_analysis.s3_downloader - INFO -   Completed: 0 downloaded, 152 skipped, 0 failed
2025-12-02 12:16:07,383 - qualicum_beach_gcp_analysis.s3_downloader - INFO - Processing manifest: input-file_172547.txt
2025-12-02 12:16:07,384 - qualicum_beach_gcp_analysis.s3_downloader - INFO -   Bucket: spexi-data-domain-assets-production-ca-central-1
2025-12-02 12:16:07,384 - qualicum_beach_gcp_analysis.s3_downloader - INFO -   S3 prefix: standardized-images/8928d89accbffff/17254

✓ Image download complete


## Step 4: Export GCPs for MetaShape


In [5]:
# Export GCPs to MetaShape XML format (preferred by MetaShape)
gcp_xml_path = output_dir / "gcps_metashape.xml"
export_to_metashape_xml(gcps, str(gcp_xml_path))
print(f"✓ GCPs exported to XML: {gcp_xml_path}")

# Also export CSV for reference
gcp_csv_path = output_dir / "gcps_metashape.csv"
export_to_metashape_csv(gcps, str(gcp_csv_path))
print(f"✓ GCPs also exported to CSV: {gcp_csv_path}")

# Use XML file for processing (MetaShape's native format)
gcp_file_path = gcp_xml_path


Exported 12 GCPs to MetaShape XML: outputs/gcps_metashape.xml
✓ GCPs exported to XML: outputs/gcps_metashape.xml
Exported 12 GCPs to MetaShape CSV: outputs/gcps_metashape.csv
✓ GCPs also exported to CSV: outputs/gcps_metashape.csv


## Step 5: Process Orthomosaic WITHOUT GCPs


In [6]:
# Ensure imports and variables are defined
if 'Path' not in locals():
    from pathlib import Path

if 'output_dir' not in locals():
    output_dir = Path("outputs")
    output_dir.mkdir(exist_ok=True)

if 'process_orthomosaic' not in locals() or 'PhotoMatchQuality' not in locals() or 'DepthMapQuality' not in locals():
    from qualicum_beach_gcp_analysis import (
        process_orthomosaic,
        PhotoMatchQuality,
        DepthMapQuality
    )

if 'photos_dir' not in locals():
    photos_dir = Path("input/images")

# Setup paths for processing
intermediate_dir = output_dir / "intermediate"
ortho_output_dir = output_dir / "orthomosaics"

# Process orthomosaic WITHOUT GCPs
# Note: clean_intermediate_files=False will reuse existing processing steps
# Set to True to start fresh and delete previous work
print("=" * 60)
print("Processing orthomosaic WITHOUT GCPs...")
print("=" * 60)

project_path_no_gcps = intermediate_dir / "orthomosaic_no_gcps.psx"

stats_no_gcps = process_orthomosaic(
    photos_dir=photos_dir,
    output_path=ortho_output_dir,
    project_path=project_path_no_gcps,
    product_id="orthomosaic_no_gcps",
    clean_intermediate_files=False,  # Reuse existing processing if available
    photo_match_quality=PhotoMatchQuality.MediumQuality,
    depth_map_quality=DepthMapQuality.MediumQuality,
    tiepoint_limit=10000,
    use_gcps=False
)

print("\n✓ Orthomosaic processing (without GCPs) complete!")
print(f"  Number of photos: {stats_no_gcps['num_photos']}")
print(f"\n📁 Output Files:")
ortho_path_no_gcps = Path(stats_no_gcps['ortho_path'])
if ortho_path_no_gcps.exists():
    file_size_mb = ortho_path_no_gcps.stat().st_size / (1024 * 1024)
    print(f"  ✓ Orthomosaic GeoTIFF: {ortho_path_no_gcps.absolute()}")
    print(f"    Size: {file_size_mb:.2f} MB")
else:
    print(f"  ✗ Orthomosaic GeoTIFF NOT FOUND at: {ortho_path_no_gcps.absolute()}")
    print(f"    Expected location: {ortho_path_no_gcps}")
    print(f"    Output directory exists: {ortho_path_no_gcps.parent.exists()}")
if 'log_file_path' in stats_no_gcps:
    print(f"  📝 Log file: {stats_no_gcps['log_file_path']}")


2025-12-02 12:16:07,448 - qualicum_beach_gcp_analysis.metashape_processor - INFO - 📝 MetaShape verbose output will be saved to: outputs/intermediate/logs/orthomosaic_no_gcps_metashape.log
2025-12-02 12:16:07,449 - qualicum_beach_gcp_analysis.metashape_processor - INFO - 📂 Loading existing project: outputs/intermediate/orthomosaic_no_gcps.psx


Processing orthomosaic WITHOUT GCPs...
LoadProject: path = outputs/intermediate/orthomosaic_no_gcps.psx


Document.open(): The document is opened in read-only mode because it is already in use.


loaded project in 0.010734 sec
SaveProject: path = outputs/intermediate/orthomosaic_no_gcps.psx
saved project in 0.152455 sec
LoadProject: path = outputs/intermediate/orthomosaic_no_gcps.psx


2025-12-02 12:16:08,776 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   ✓ Project opened in writable mode
2025-12-02 12:16:08,779 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Found existing chunk with 1841 cameras


loaded project in 0.264611 sec


2025-12-02 12:16:08,781 - qualicum_beach_gcp_analysis.metashape_processor - INFO - Processing status:
2025-12-02 12:16:08,783 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Photos added: True
2025-12-02 12:16:08,784 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Photos matched: True
2025-12-02 12:16:08,786 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Cameras aligned: True
2025-12-02 12:16:08,787 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Depth maps built: True
2025-12-02 12:16:08,788 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Model built: True
2025-12-02 12:16:08,791 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Orthomosaic built: True
2025-12-02 12:16:08,792 - qualicum_beach_gcp_analysis.metashape_processor - INFO - ✓ Photos already added (1841 cameras)
2025-12-02 12:16:08,795 - qualicum_beach_gcp_analysis.metashape_processor - INFO - ✓ Photos already matched (1956517 tie points)
2025-12-02 


✓ Orthomosaic processing (without GCPs) complete!
  Number of photos: 1841

📁 Output Files:
  ✓ Orthomosaic GeoTIFF: /Users/mauriciohessflores/Documents/Code/MyCode/research-qualicum_beach_gcp_analysis/outputs/orthomosaics/orthomosaic_no_gcps.tif
    Size: 12959.35 MB
  📝 Log file: outputs/intermediate/logs/orthomosaic_no_gcps_metashape.log


## Step 6: Process Orthomosaic WITH GCPs


In [7]:
# Process orthomosaic WITH GCPs
# Ensure imports and variables are defined
if 'Path' not in locals():
    from pathlib import Path

if 'output_dir' not in locals():
    output_dir = Path("outputs")
    output_dir.mkdir(exist_ok=True)

if 'process_orthomosaic' not in locals() or 'PhotoMatchQuality' not in locals() or 'DepthMapQuality' not in locals():
    from qualicum_beach_gcp_analysis import (
        process_orthomosaic,
        PhotoMatchQuality,
        DepthMapQuality
    )

if 'photos_dir' not in locals():
    photos_dir = Path("input/images")

# Setup paths for processing
intermediate_dir = output_dir / "intermediate"
ortho_output_dir = output_dir / "orthomosaics"

# Note: clean_intermediate_files=False will reuse existing processing steps
# Set to True to start fresh and delete previous work
print("=" * 60)
print("Processing orthomosaic WITH GCPs...")
print("=" * 60)

project_path_with_gcps = intermediate_dir / "orthomosaic_with_gcps.psx"

# Use XML file (MetaShape's native format) - defined in Step 4
gcp_file_for_processing = output_dir / "gcps_metashape.xml"

stats_with_gcps = process_orthomosaic(
    photos_dir=photos_dir,
    output_path=ortho_output_dir,
    project_path=project_path_with_gcps,
    gcp_file=gcp_file_for_processing,  # Use XML file (MetaShape's native format)
    product_id="orthomosaic_with_gcps",
    clean_intermediate_files=False,  # Reuse existing processing if available
    photo_match_quality=PhotoMatchQuality.MediumQuality,
    depth_map_quality=DepthMapQuality.MediumQuality,
    tiepoint_limit=10000,
    use_gcps=True,
    gcp_accuracy=0.05,  # High accuracy (5cm) for high weight in bundle adjustment
)

print("\n✓ Orthomosaic processing (with GCPs) complete!")
print(f"  Number of photos: {stats_with_gcps['num_photos']}")
print(f"  Number of markers: {stats_with_gcps.get('num_markers', 0)}")
print(f"\n📁 Output Files:")
ortho_path_with_gcps = Path(stats_with_gcps['ortho_path'])
if ortho_path_with_gcps.exists():
    file_size_mb = ortho_path_with_gcps.stat().st_size / (1024 * 1024)
    print(f"  ✓ Orthomosaic GeoTIFF: {ortho_path_with_gcps.absolute()}")
    print(f"    Size: {file_size_mb:.2f} MB")
else:
    print(f"  ✗ Orthomosaic GeoTIFF NOT FOUND at: {ortho_path_with_gcps.absolute()}")
    print(f"    Expected location: {ortho_path_with_gcps}")
    print(f"    Output directory exists: {ortho_path_with_gcps.parent.exists()}")
if 'log_file_path' in stats_with_gcps:
    print(f"  📝 Log file: {stats_with_gcps['log_file_path']}")


2025-12-02 12:16:08,819 - qualicum_beach_gcp_analysis.metashape_processor - INFO - 📝 MetaShape verbose output will be saved to: outputs/intermediate/logs/orthomosaic_with_gcps_metashape.log
2025-12-02 12:16:08,820 - qualicum_beach_gcp_analysis.metashape_processor - INFO - 📂 Loading existing project: outputs/intermediate/orthomosaic_with_gcps.psx


Processing orthomosaic WITH GCPs...
LoadProject: path = outputs/intermediate/orthomosaic_with_gcps.psx


Document.open(): The document is opened in read-only mode because it is already in use.


loaded project in 0.001899 sec
SaveProject: path = outputs/intermediate/orthomosaic_with_gcps.psx
saved project in 0.115173 sec
LoadProject: path = outputs/intermediate/orthomosaic_with_gcps.psx
loaded project in 0.083886 sec


2025-12-02 12:16:09,936 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   ✓ Project opened in writable mode
2025-12-02 12:16:09,938 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Found existing chunk with 1841 cameras
2025-12-02 12:16:09,941 - qualicum_beach_gcp_analysis.metashape_processor - INFO - Processing status:
2025-12-02 12:16:09,943 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Photos added: True
2025-12-02 12:16:09,944 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Photos matched: False
2025-12-02 12:16:09,944 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Cameras aligned: False
2025-12-02 12:16:09,945 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Depth maps built: False
2025-12-02 12:16:09,947 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Model built: False
2025-12-02 12:16:09,947 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Orthomosaic built: False
2025-12-02 12

...

SaveProject: path = outputs/intermediate/orthomosaic_with_gcps.psx
saved project in 6.5e-05 sec
LoadProject: path = outputs/intermediate/orthomosaic_with_gcps.psx
loaded project in 0.106392 sec
BuildModel: source data = Depth maps, surface type = Arbitrary, face count = High, volumetric masking = 0, OOC version, interpolation = Enabled, vertex colors = 1
Compression level: 1
Preparing depth maps...
1796 depth maps
scheduled 90 depth map groups (1796 cameras)
saved camera partition in 0.001016 sec
loaded camera partition in 0.000308 sec
saved group #1/90: done in 0.913409 s, 20 cameras, 62.2408 MB data, 24.1406 KB registry
loaded camera partition in 0.000174 sec
saved group #2/90: done in 0.94005 s, 20 cameras, 64.9403 MB data, 24.1406 KB registry
loaded camera partition in 0.000192 sec
saved group #3/90: done in 0.914889 s, 20 cameras, 61.9803 MB data, 24.1406 KB registry
loaded camera partition in 0.000191 sec
saved group #4/90: done in 0.912652 s, 20 cameras, 63.5981 MB data, 24.1406

2025-12-02 14:47:43,242 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   ✓ 3D model built successfully
2025-12-02 14:47:43,244 - qualicum_beach_gcp_analysis.metashape_processor - INFO - Building orthomosaic...


SaveProject: path = outputs/intermediate/orthomosaic_with_gcps.psx
saved project in 0.000239 sec
LoadProject: path = outputs/intermediate/orthomosaic_with_gcps.psx
loaded project in 0.134903 sec
BuildOrthomosaic: surface = Mesh, blending mode = Mosaic, fill holes = 1, ghosting filter = 0, cull faces = 0, refine seamlines = 0, resolution = 0
initializing...
tessellating mesh... done (22701584 -> 22701584 faces)
generating 54587x46449 orthomosaic (10 levels, 0.0292782 resolution)
selected 1799 cameras
saved orthomosaic data in 0.000821 sec
saved camera partition in 0.0011 sec
scheduled 90 orthophoto groups
loaded camera partition in 7e-05 sec
tessellating mesh... done (22701584 -> 22701584 faces)
loaded orthomosaic data in 2.58541 sec
Orthorectifying 20 images
8928d89ac0bffff_172555_0001: 4999x5730 -> 3368x4037
8928d89ac0bffff_172555_0002: 4999x5981 -> 3427x4069
8928d89ac0bffff_172555_0004: 4952x5987 -> 3516x4219
8928d89ac0bffff_172555_0003: 5804x5987 -> 3482x4179
8928d89ac0bffff_172555_

2025-12-02 15:01:36,301 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   ✓ Orthomosaic built successfully
2025-12-02 15:01:36,304 - qualicum_beach_gcp_analysis.metashape_processor - INFO - ✓ Orthomosaic GeoTIFF already exists: outputs/orthomosaics/orthomosaic_with_gcps.tif
2025-12-02 15:01:36,305 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   File size: 13004.85 MB
2025-12-02 15:01:36,306 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Skipping export (use clean_intermediate_files=True to force re-export)
2025-12-02 15:01:36,309 - qualicum_beach_gcp_analysis.metashape_processor - INFO - ✅ MetaShape processing completed successfully
2025-12-02 15:01:36,310 - qualicum_beach_gcp_analysis.metashape_processor - INFO - 📄 Full verbose log saved to: outputs/intermediate/logs/orthomosaic_with_gcps_metashape.log



✓ Orthomosaic processing (with GCPs) complete!
  Number of photos: 1841
  Number of markers: 12

📁 Output Files:
  ✓ Orthomosaic GeoTIFF: /Users/mauriciohessflores/Documents/Code/MyCode/research-qualicum_beach_gcp_analysis/outputs/orthomosaics/orthomosaic_with_gcps.tif
    Size: 13004.85 MB
  📝 Log file: outputs/intermediate/logs/orthomosaic_with_gcps_metashape.log


## Step 7: Compare Orthomosaics to Reference Basemaps

### Comparison Methodology

The orthomosaics are compared to reference basemaps (ESRI World Imagery and OpenStreetMap) using a comprehensive methodology:

#### 1. **Reprojection and Alignment**
   - The orthomosaic is reprojected to match the reference basemap's coordinate reference system (CRS) and spatial extent
   - Bilinear resampling is used to ensure pixel-level alignment
   - Both rasters are normalized to the same spatial resolution

#### 2. **Pixel-level Error Metrics**
   - **RMSE (Root Mean Square Error)**: Measures overall pixel intensity differences between orthomosaic and reference
   - **MAE (Mean Absolute Error)**: Measures average absolute pixel differences
   - **Structural Similarity**: Correlation-based measure indicating how well the orthomosaic structure matches the reference

#### 3. **2D Spatial Error (Feature Matching)**
   - Feature-based matching (SIFT, ORB, or phase correlation) identifies corresponding points between orthomosaic and reference
   - Computes X and Y pixel offsets, providing 2D spatial error measurements
   - This identifies systematic shifts, rotations, or misalignments that pixel-level metrics might miss
   - The method automatically selects the best available algorithm (SIFT > ORB > phase correlation > template matching)

#### 4. **Seamline Detection**
   - Gradient-based analysis detects potential seamline artifacts
   - Identifies high-gradient regions that may indicate stitching errors or discontinuities
   - Reports percentage of pixels flagged as potential seamlines

#### 5. **Comparison Process**
   - Both orthomosaics (with and without GCPs) are compared against the same reference basemap
   - Metrics are computed for each band and averaged for overall statistics
   - Results are saved to JSON files for persistence and later analysis


## Step 7: Compare Orthomosaics to Reference Basemaps


In [8]:
# Compare against ESRI basemap
# Ensure imports and variables are defined
if 'Path' not in locals():
    from pathlib import Path

if 'compare_orthomosaic_to_basemap' not in locals():
    from qualicum_beach_gcp_analysis import compare_orthomosaic_to_basemap

if 'output_dir' not in locals():
    output_dir = Path("outputs")

print("=" * 60)
print("Comparing orthomosaics to ESRI World Imagery basemap...")
print("=" * 60)

comparison_dir = output_dir / "comparisons"

# Ensure basemap paths are defined (from Step 2)
if 'basemap_esri_path' not in locals():
    basemap_esri_path = str(output_dir / "qualicum_beach_basemap_esri.tif")

# Determine orthomosaic paths - use stats if available, otherwise find files directly
if 'stats_no_gcps' in locals() and 'ortho_path' in stats_no_gcps:
    ortho_no_gcps_path = Path(stats_no_gcps['ortho_path'])
else:
    # Try to find the orthomosaic file directly
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_no_gcps_path = ortho_output_dir / "orthomosaic_no_gcps.tif"
    if not ortho_no_gcps_path.exists():
        raise FileNotFoundError(f"Orthomosaic (no GCPs) not found at: {ortho_no_gcps_path.absolute()}\n"
                               f"Please run Step 5 first, or ensure the file exists at this location.")

if 'stats_with_gcps' in locals() and 'ortho_path' in stats_with_gcps:
    ortho_with_gcps_path = Path(stats_with_gcps['ortho_path'])
else:
    # Try to find the orthomosaic file directly
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_with_gcps_path = ortho_output_dir / "orthomosaic_with_gcps.tif"
    if not ortho_with_gcps_path.exists():
        raise FileNotFoundError(f"Orthomosaic (with GCPs) not found at: {ortho_with_gcps_path.absolute()}\n"
                               f"Please run Step 6 first, or ensure the file exists at this location.")

print(f"Using orthomosaic (no GCPs): {ortho_no_gcps_path}")
print(f"Using orthomosaic (with GCPs): {ortho_with_gcps_path}")

# Compare without GCPs
print("\nComparing orthomosaic (without GCPs) to ESRI basemap...")
metrics_no_gcps_esri = compare_orthomosaic_to_basemap(
    ortho_path=ortho_no_gcps_path,
    basemap_path=Path(basemap_esri_path),
    output_dir=comparison_dir
)

# Compare with GCPs
print("\nComparing orthomosaic (with GCPs) to ESRI basemap...")
metrics_with_gcps_esri = compare_orthomosaic_to_basemap(
    ortho_path=ortho_with_gcps_path,
    basemap_path=Path(basemap_esri_path),
    output_dir=comparison_dir
)

print("\n✓ ESRI comparison complete!")

# Save metrics to JSON files for later use
import json
from qualicum_beach_gcp_analysis.report_generator import convert_to_json_serializable

metrics_dir = comparison_dir / "metrics"
metrics_dir.mkdir(parents=True, exist_ok=True)

# Save ESRI metrics
metrics_no_gcps_esri_serializable = convert_to_json_serializable(metrics_no_gcps_esri)
metrics_with_gcps_esri_serializable = convert_to_json_serializable(metrics_with_gcps_esri)

with open(metrics_dir / "metrics_no_gcps_esri.json", 'w') as f:
    json.dump(metrics_no_gcps_esri_serializable, f, indent=2)
with open(metrics_dir / "metrics_with_gcps_esri.json", 'w') as f:
    json.dump(metrics_with_gcps_esri_serializable, f, indent=2)

print(f"✓ Metrics saved to: {metrics_dir}")


2025-12-02 15:01:36,800 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Comparing orthomosaic orthomosaic_no_gcps.tif to basemap qualicum_beach_basemap_esri.tif


Comparing orthomosaics to ESRI World Imagery basemap...
Using orthomosaic (no GCPs): outputs/orthomosaics/orthomosaic_no_gcps.tif
Using orthomosaic (with GCPs): outputs/orthomosaics/orthomosaic_with_gcps.tif

Comparing orthomosaic (without GCPs) to ESRI basemap...


2025-12-02 15:01:54,991 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Saved reprojected raster to: outputs/comparisons/reprojected_orthomosaic_no_gcps.tif
2025-12-02 15:01:55,141 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Feature matching (sift) shift (-38.7, -25.3) too large, rejecting
2025-12-02 15:01:55,167 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Feature matching (orb): 15 matches, offset=(0.90, -16.45) px, RMSE_2D=25.97 px
2025-12-02 15:01:55,168 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Phase correlation failed: local variable 'phase_cross_correlation' referenced before assignment
2025-12-02 15:01:55,174 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Template matching shift (-64.0, -22.0) too large, rejecting
2025-12-02 15:01:55,178 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Comparison complete. Overall RMSE: 10.151322773354906
2025-12-02 15:01:55,178 - qualicum_beach_gcp_analysis.quality_metrics - INFO 


Comparing orthomosaic (with GCPs) to ESRI basemap...


2025-12-02 15:02:12,807 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Saved reprojected raster to: outputs/comparisons/reprojected_orthomosaic_with_gcps.tif
2025-12-02 15:02:12,959 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Feature matching (sift): 13 matches, offset=(-6.36, 18.85) px, RMSE_2D=83.46 px
2025-12-02 15:02:12,982 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Feature matching (orb): 14 matches, offset=(-1.98, -5.66) px, RMSE_2D=18.70 px
2025-12-02 15:02:12,983 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Phase correlation failed: local variable 'phase_cross_correlation' referenced before assignment
2025-12-02 15:02:12,988 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Template matching shift (-64.0, -22.0) too large, rejecting
2025-12-02 15:02:12,994 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Comparison complete. Overall RMSE: 10.159717849686071



✓ ESRI comparison complete!
✓ Metrics saved to: outputs/comparisons/metrics


## Step 7.5: Apply 2D Shift Alignment and Re-analyze

After the initial comparison, we apply 2D shifts to align the orthomosaics with the ESRI basemap using feature matching, then re-analyze accuracy and seamlines to see if alignment improves the results.


In [9]:
# Step 7.5: Apply 2D Shift Alignment and Re-analyze
# Ensure imports and variables are defined
if 'Path' not in locals():
    from pathlib import Path
if 'json' not in locals():
    import json

if 'apply_2d_shift_to_orthomosaic' not in locals() or 'compare_orthomosaic_to_basemap' not in locals():
    from qualicum_beach_gcp_analysis import (
        apply_2d_shift_to_orthomosaic,
        compare_orthomosaic_to_basemap
    )

if 'output_dir' not in locals():
    output_dir = Path("outputs")
if 'comparison_dir' not in locals():
    comparison_dir = output_dir / "comparisons"
if 'basemap_esri_path' not in locals():
    basemap_esri_path = str(output_dir / "qualicum_beach_basemap_esri.tif")

# Ensure orthomosaic paths are defined
if 'ortho_no_gcps_path' not in locals():
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_no_gcps_path = ortho_output_dir / "orthomosaic_no_gcps.tif"
if 'ortho_with_gcps_path' not in locals():
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_with_gcps_path = ortho_output_dir / "orthomosaic_with_gcps.tif"

print("=" * 60)
print("Step 7.5: Apply 2D Shift Alignment and Re-analyze")
print("=" * 60)

# Create directory for shifted orthomosaics
shifted_dir = output_dir / "orthomosaics_shifted"
shifted_dir.mkdir(parents=True, exist_ok=True)

# Apply 2D shift to orthomosaic without GCPs
print("\n1. Applying 2D shift to orthomosaic (without GCPs)...")
shifted_no_gcps_path = shifted_dir / "orthomosaic_no_gcps_shifted.tif"
_, shift_info_no_gcps = apply_2d_shift_to_orthomosaic(
    ortho_path=Path(ortho_no_gcps_path),
    reference_path=Path(basemap_esri_path),
    output_path=shifted_no_gcps_path
)
print(f"   Shift applied: X={shift_info_no_gcps['shift_x_pixels']:.2f} px, Y={shift_info_no_gcps['shift_y_pixels']:.2f} px")

# Apply 2D shift to orthomosaic with GCPs
print("\n2. Applying 2D shift to orthomosaic (with GCPs)...")
shifted_with_gcps_path = shifted_dir / "orthomosaic_with_gcps_shifted.tif"
_, shift_info_with_gcps = apply_2d_shift_to_orthomosaic(
    ortho_path=Path(ortho_with_gcps_path),
    reference_path=Path(basemap_esri_path),
    output_path=shifted_with_gcps_path
)
print(f"   Shift applied: X={shift_info_with_gcps['shift_x_pixels']:.2f} px, Y={shift_info_with_gcps['shift_y_pixels']:.2f} px")

# Re-analyze shifted orthomosaics
print("\n3. Re-analyzing shifted orthomosaics against ESRI basemap...")

# Compare shifted orthomosaic (without GCPs)
print("\n   Analyzing shifted orthomosaic (without GCPs)...")
metrics_shifted_no_gcps = compare_orthomosaic_to_basemap(
    ortho_path=shifted_no_gcps_path,
    basemap_path=Path(basemap_esri_path),
    output_dir=comparison_dir
)

# Compare shifted orthomosaic (with GCPs)
print("\n   Analyzing shifted orthomosaic (with GCPs)...")
metrics_shifted_with_gcps = compare_orthomosaic_to_basemap(
    ortho_path=shifted_with_gcps_path,
    basemap_path=Path(basemap_esri_path),
    output_dir=comparison_dir
)

# Save shifted metrics
metrics_dir = comparison_dir / "metrics"
metrics_dir.mkdir(parents=True, exist_ok=True)

shifted_metrics_file_no_gcps = metrics_dir / "metrics_shifted_no_gcps_esri.json"
shifted_metrics_file_with_gcps = metrics_dir / "metrics_shifted_with_gcps_esri.json"

with open(shifted_metrics_file_no_gcps, 'w') as f:
    json.dump(metrics_shifted_no_gcps, f, indent=2, default=str)
with open(shifted_metrics_file_with_gcps, 'w') as f:
    json.dump(metrics_shifted_with_gcps, f, indent=2, default=str)

print(f"\n✓ Shifted metrics saved to: {metrics_dir}")

# Compare initial vs shifted results
print("\n4. Comparing initial vs. shifted results...")

# Load initial metrics if not available
if 'metrics_no_gcps_esri' not in locals() or 'metrics_with_gcps_esri' not in locals():
    metrics_file_no_gcps = metrics_dir / "metrics_no_gcps_esri.json"
    metrics_file_with_gcps = metrics_dir / "metrics_with_gcps_esri.json"
    if metrics_file_no_gcps.exists() and metrics_file_with_gcps.exists():
        with open(metrics_file_no_gcps, 'r') as f:
            metrics_no_gcps_esri = json.load(f)
        with open(metrics_file_with_gcps, 'r') as f:
            metrics_with_gcps_esri = json.load(f)
    else:
        raise NameError("Initial metrics not found. Please run Step 7 first.")

# Calculate improvements from shifting
initial_no_gcps = metrics_no_gcps_esri.get('overall', {})
shifted_no_gcps = metrics_shifted_no_gcps.get('overall', {})
initial_with_gcps = metrics_with_gcps_esri.get('overall', {})
shifted_with_gcps = metrics_shifted_with_gcps.get('overall', {})

print("\n   Without GCPs:")
if initial_no_gcps.get('rmse') and shifted_no_gcps.get('rmse'):
    rmse_improvement = ((initial_no_gcps['rmse'] - shifted_no_gcps['rmse']) / initial_no_gcps['rmse']) * 100
    print(f"     RMSE: {initial_no_gcps['rmse']:.4f} → {shifted_no_gcps['rmse']:.4f} ({rmse_improvement:+.2f}%)")
if initial_no_gcps.get('seamline_percentage') and shifted_no_gcps.get('seamline_percentage'):
    seamline_improvement = initial_no_gcps['seamline_percentage'] - shifted_no_gcps['seamline_percentage']
    print(f"     Seamlines: {initial_no_gcps['seamline_percentage']:.2f}% → {shifted_no_gcps['seamline_percentage']:.2f}% ({seamline_improvement:+.2f}%)")

print("\n   With GCPs:")
if initial_with_gcps.get('rmse') and shifted_with_gcps.get('rmse'):
    rmse_improvement = ((initial_with_gcps['rmse'] - shifted_with_gcps['rmse']) / initial_with_gcps['rmse']) * 100
    print(f"     RMSE: {initial_with_gcps['rmse']:.4f} → {shifted_with_gcps['rmse']:.4f} ({rmse_improvement:+.2f}%)")
if initial_with_gcps.get('seamline_percentage') and shifted_with_gcps.get('seamline_percentage'):
    seamline_improvement = initial_with_gcps['seamline_percentage'] - shifted_with_gcps['seamline_percentage']
    print(f"     Seamlines: {initial_with_gcps['seamline_percentage']:.2f}% → {shifted_with_gcps['seamline_percentage']:.2f}% ({seamline_improvement:+.2f}%)")

print("\n✓ Step 7.5 complete!")


2025-12-02 15:02:13,006 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Reprojecting orthomosaic to match reference...


Step 7.5: Apply 2D Shift Alignment and Re-analyze

1. Applying 2D shift to orthomosaic (without GCPs)...


2025-12-02 15:02:29,625 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Computing 2D shift using feature matching...
2025-12-02 15:02:29,642 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Feature matching (sift) shift (-38.7, -25.3) too large, rejecting
2025-12-02 15:02:29,667 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Feature matching (orb): 15 matches, offset=(0.90, -16.45) px, RMSE_2D=25.97 px
2025-12-02 15:02:29,667 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Method orb found shift: (0.90, -16.45) px, confidence=0.103
2025-12-02 15:02:29,675 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Line/edge matching: offset=(0.90, 0.80) px, error=1.0000
2025-12-02 15:02:29,676 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Phase correlation failed: local variable 'phase_cross_correlation' referenced before assignment
2025-12-02 15:02:29,681 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Template matching shift (-64.0, -22

   Shift applied: X=0.90 px, Y=-16.45 px

2. Applying 2D shift to orthomosaic (with GCPs)...


2025-12-02 15:02:45,177 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Computing 2D shift using feature matching...
2025-12-02 15:02:45,200 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Feature matching (sift): 13 matches, offset=(-6.36, 18.85) px, RMSE_2D=83.46 px
2025-12-02 15:02:45,201 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Method sift found shift: (-6.36, 18.85) px, confidence=0.051
2025-12-02 15:02:45,224 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Feature matching (orb): 14 matches, offset=(-1.98, -5.66) px, RMSE_2D=18.70 px
2025-12-02 15:02:45,226 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Method orb found shift: (-1.98, -5.66) px, confidence=0.109
2025-12-02 15:02:45,230 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Line/edge matching: offset=(0.90, 0.80) px, error=1.0000
2025-12-02 15:02:45,231 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Phase correlation failed: local variable 'phase_cross_correlat

   Shift applied: X=-1.98 px, Y=-5.66 px

3. Re-analyzing shifted orthomosaics against ESRI basemap...

   Analyzing shifted orthomosaic (without GCPs)...

   Analyzing shifted orthomosaic (with GCPs)...

✓ Shifted metrics saved to: outputs/comparisons/metrics

4. Comparing initial vs. shifted results...

   Without GCPs:
     RMSE: 10.1513 → 10.3752 (-2.21%)
     Seamlines: 9.94% → 11.63% (-1.69%)

   With GCPs:
     RMSE: 10.1597 → 10.2660 (-1.05%)
     Seamlines: 9.94% → 11.38% (-1.44%)

✓ Step 7.5 complete!


## Step 7.6: Align Orthomosaics to Ground Control Points and Re-analyze

In addition to feature-matching alignment, we also align the orthomosaics directly to the ground control points (GCPs) using their known coordinates. This provides an alternative alignment method that can be compared against feature-matching alignment.


In [10]:
# Step 7.6: Align Orthomosaics to Ground Control Points and Re-analyze
# Ensure imports and variables are defined
if 'Path' not in locals():
    from pathlib import Path
if 'json' not in locals():
    import json

if 'align_orthomosaic_to_gcps' not in locals() or 'compare_orthomosaic_to_basemap' not in locals():
    from qualicum_beach_gcp_analysis import (
        align_orthomosaic_to_gcps,
        compare_orthomosaic_to_basemap
    )

if 'load_gcps_from_kmz' not in locals():
    from qualicum_beach_gcp_analysis import load_gcps_from_kmz

if 'output_dir' not in locals():
    output_dir = Path("outputs")
if 'comparison_dir' not in locals():
    comparison_dir = output_dir / "comparisons"
if 'basemap_esri_path' not in locals():
    basemap_esri_path = str(output_dir / "qualicum_beach_basemap_esri.tif")

# Ensure orthomosaic paths are defined
if 'ortho_no_gcps_path' not in locals():
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_no_gcps_path = ortho_output_dir / "orthomosaic_no_gcps.tif"
if 'ortho_with_gcps_path' not in locals():
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_with_gcps_path = ortho_output_dir / "orthomosaic_with_gcps.tif"

# Load GCPs if not already loaded
if 'gcps' not in locals():
    # Try to find KMZ file
    kmz_path = Path("input") / "QualicumBeach_AOI.kmz"
    if not kmz_path.exists():
        # Try alternative location
        kmz_path = Path("/Users/mauriciohessflores/Documents/Code/Data/Qualicum Beach GCPs/Spexi_Survey_Points/Spexi_Drone_Survey/QualicumBeach_AOI.kmz")
    
    if kmz_path.exists():
        gcps = load_gcps_from_kmz(str(kmz_path))
        print(f"Loaded {len(gcps)} GCPs from {kmz_path}")
    else:
        raise FileNotFoundError(f"Could not find GCP KMZ file. Tried: {kmz_path}")

print("=" * 60)
print("Step 7.6: Align Orthomosaics to Ground Control Points")
print("=" * 60)

# Create directory for GCP-aligned orthomosaics
gcp_aligned_dir = output_dir / "orthomosaics_gcp_aligned"
gcp_aligned_dir.mkdir(parents=True, exist_ok=True)

# Align orthomosaic without GCPs to GCPs
print("\n1. Aligning orthomosaic (without GCPs) to GCPs...")
gcp_aligned_no_gcps_path = gcp_aligned_dir / "orthomosaic_no_gcps_gcp_aligned.tif"
_, alignment_info_no_gcps = align_orthomosaic_to_gcps(
    ortho_path=Path(ortho_no_gcps_path),
    reference_path=Path(basemap_esri_path),
    gcps=gcps,
    output_path=gcp_aligned_no_gcps_path
)
print(f"   Alignment RMSE: {alignment_info_no_gcps['rmse_total_pixels']:.2f} pixels")
print(f"   Used {alignment_info_no_gcps['num_gcps_used']} GCPs")

# Align orthomosaic with GCPs to GCPs
print("\n2. Aligning orthomosaic (with GCPs) to GCPs...")
gcp_aligned_with_gcps_path = gcp_aligned_dir / "orthomosaic_with_gcps_gcp_aligned.tif"
_, alignment_info_with_gcps = align_orthomosaic_to_gcps(
    ortho_path=Path(ortho_with_gcps_path),
    reference_path=Path(basemap_esri_path),
    gcps=gcps,
    output_path=gcp_aligned_with_gcps_path
)
print(f"   Alignment RMSE: {alignment_info_with_gcps['rmse_total_pixels']:.2f} pixels")
print(f"   Used {alignment_info_with_gcps['num_gcps_used']} GCPs")

# Re-analyze GCP-aligned orthomosaics
print("\n3. Re-analyzing GCP-aligned orthomosaics against ESRI basemap...")

# Compare GCP-aligned orthomosaic (without GCPs)
print("\n   Analyzing GCP-aligned orthomosaic (without GCPs)...")
metrics_gcp_aligned_no_gcps = compare_orthomosaic_to_basemap(
    ortho_path=gcp_aligned_no_gcps_path,
    basemap_path=Path(basemap_esri_path),
    output_dir=comparison_dir
)

# Compare GCP-aligned orthomosaic (with GCPs)
print("\n   Analyzing GCP-aligned orthomosaic (with GCPs)...")
metrics_gcp_aligned_with_gcps = compare_orthomosaic_to_basemap(
    ortho_path=gcp_aligned_with_gcps_path,
    basemap_path=Path(basemap_esri_path),
    output_dir=comparison_dir
)

# Save GCP-aligned metrics
metrics_dir = comparison_dir / "metrics"
metrics_dir.mkdir(parents=True, exist_ok=True)

gcp_aligned_metrics_file_no_gcps = metrics_dir / "metrics_gcp_aligned_no_gcps_esri.json"
gcp_aligned_metrics_file_with_gcps = metrics_dir / "metrics_gcp_aligned_with_gcps_esri.json"

with open(gcp_aligned_metrics_file_no_gcps, 'w') as f:
    json.dump(metrics_gcp_aligned_no_gcps, f, indent=2, default=str)
with open(gcp_aligned_metrics_file_with_gcps, 'w') as f:
    json.dump(metrics_gcp_aligned_with_gcps, f, indent=2, default=str)

print(f"\n✓ GCP-aligned metrics saved to: {metrics_dir}")

# Compare alignment methods
print("\n4. Comparing alignment methods...")

# Load initial and shifted metrics if available
if 'metrics_no_gcps_esri' not in locals() or 'metrics_with_gcps_esri' not in locals():
    metrics_file_no_gcps = metrics_dir / "metrics_no_gcps_esri.json"
    metrics_file_with_gcps = metrics_dir / "metrics_with_gcps_esri.json"
    if metrics_file_no_gcps.exists() and metrics_file_with_gcps.exists():
        with open(metrics_file_no_gcps, 'r') as f:
            metrics_no_gcps_esri = json.load(f)
        with open(metrics_file_with_gcps, 'r') as f:
            metrics_with_gcps_esri = json.load(f)

# Load shifted metrics if available
shifted_metrics_file_no_gcps = metrics_dir / "metrics_shifted_no_gcps_esri.json"
shifted_metrics_file_with_gcps = metrics_dir / "metrics_shifted_with_gcps_esri.json"
metrics_shifted_no_gcps = None
metrics_shifted_with_gcps = None
if shifted_metrics_file_no_gcps.exists() and shifted_metrics_file_with_gcps.exists():
    with open(shifted_metrics_file_no_gcps, 'r') as f:
        metrics_shifted_no_gcps = json.load(f)
    with open(shifted_metrics_file_with_gcps, 'r') as f:
        metrics_shifted_with_gcps = json.load(f)

print("\n   Without GCPs - RMSE comparison:")
initial_no = metrics_no_gcps_esri.get('overall', {}) if 'metrics_no_gcps_esri' in locals() else {}
shifted_no = metrics_shifted_no_gcps.get('overall', {}) if metrics_shifted_no_gcps else {}
gcp_aligned_no = metrics_gcp_aligned_no_gcps.get('overall', {})

if initial_no.get('rmse'):
    print(f"     Initial:        {initial_no['rmse']:.4f}")
if shifted_no.get('rmse'):
    print(f"     Feature-matched: {shifted_no['rmse']:.4f}")
if gcp_aligned_no.get('rmse'):
    print(f"     GCP-aligned:     {gcp_aligned_no['rmse']:.4f}")

print("\n   With GCPs - RMSE comparison:")
initial_with = metrics_with_gcps_esri.get('overall', {}) if 'metrics_with_gcps_esri' in locals() else {}
shifted_with = metrics_shifted_with_gcps.get('overall', {}) if metrics_shifted_with_gcps else {}
gcp_aligned_with = metrics_gcp_aligned_with_gcps.get('overall', {})

if initial_with.get('rmse'):
    print(f"     Initial:        {initial_with['rmse']:.4f}")
if shifted_with.get('rmse'):
    print(f"     Feature-matched: {shifted_with['rmse']:.4f}")
if gcp_aligned_with.get('rmse'):
    print(f"     GCP-aligned:     {gcp_aligned_with['rmse']:.4f}")

print("\n✓ Step 7.6 complete!")


2025-12-02 15:02:45,372 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Aligning orthomosaic to 12 GCPs...
2025-12-02 15:02:45,372 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Reprojecting orthomosaic to match reference...


Step 7.6: Align Orthomosaics to Ground Control Points

1. Aligning orthomosaic (without GCPs) to GCPs...


2025-12-02 15:03:00,222 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Using 12 GCPs for alignment
2025-12-02 15:03:00,223 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Affine transformation computed:
2025-12-02 15:03:00,223 - qualicum_beach_gcp_analysis.quality_metrics - INFO -   X: 1.000000*x + 0.000000*y + 0.000000
2025-12-02 15:03:00,223 - qualicum_beach_gcp_analysis.quality_metrics - INFO -   Y: 0.000000*x + 1.000000*y + -0.000000
2025-12-02 15:03:00,223 - qualicum_beach_gcp_analysis.quality_metrics - INFO -   RMSE: X=0.00 px, Y=0.00 px, Total=0.00 px
2025-12-02 15:03:00,230 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Aligned orthomosaic saved to: outputs/orthomosaics_gcp_aligned/orthomosaic_no_gcps_gcp_aligned.tif
2025-12-02 15:03:00,230 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Alignment RMSE: 0.00 pixels
2025-12-02 15:03:00,231 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Aligning orthomosaic to 12 GCPs...
2025-12-02 15:03:00,2

   Alignment RMSE: 0.00 pixels
   Used 12 GCPs

2. Aligning orthomosaic (with GCPs) to GCPs...


2025-12-02 15:03:15,347 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Using 12 GCPs for alignment
2025-12-02 15:03:15,347 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Affine transformation computed:
2025-12-02 15:03:15,347 - qualicum_beach_gcp_analysis.quality_metrics - INFO -   X: 1.000000*x + 0.000000*y + 0.000000
2025-12-02 15:03:15,347 - qualicum_beach_gcp_analysis.quality_metrics - INFO -   Y: 0.000000*x + 1.000000*y + -0.000000
2025-12-02 15:03:15,348 - qualicum_beach_gcp_analysis.quality_metrics - INFO -   RMSE: X=0.00 px, Y=0.00 px, Total=0.00 px
2025-12-02 15:03:15,354 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Aligned orthomosaic saved to: outputs/orthomosaics_gcp_aligned/orthomosaic_with_gcps_gcp_aligned.tif
2025-12-02 15:03:15,354 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Alignment RMSE: 0.00 pixels
2025-12-02 15:03:15,356 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Comparing orthomosaic orthomosaic_no_gcps_gcp_aligned.

   Alignment RMSE: 0.00 pixels
   Used 12 GCPs

3. Re-analyzing GCP-aligned orthomosaics against ESRI basemap...

   Analyzing GCP-aligned orthomosaic (without GCPs)...

   Analyzing GCP-aligned orthomosaic (with GCPs)...

✓ GCP-aligned metrics saved to: outputs/comparisons/metrics

4. Comparing alignment methods...

   Without GCPs - RMSE comparison:
     Initial:        10.1513
     Feature-matched: 10.3752
     GCP-aligned:     10.1513

   With GCPs - RMSE comparison:
     Initial:        10.1597
     Feature-matched: 10.2660
     GCP-aligned:     10.1597

✓ Step 7.6 complete!


In [11]:
# Compare against OpenStreetMap basemap
# Ensure imports and variables are defined
if 'Path' not in locals():
    from pathlib import Path

if 'compare_orthomosaic_to_basemap' not in locals():
    from qualicum_beach_gcp_analysis import compare_orthomosaic_to_basemap

if 'output_dir' not in locals():
    output_dir = Path("outputs")
if 'comparison_dir' not in locals():
    comparison_dir = output_dir / "comparisons"
if 'basemap_osm_path' not in locals():
    basemap_osm_path = str(output_dir / "qualicum_beach_basemap_osm.tif")

print("=" * 60)
print("Comparing orthomosaics to OpenStreetMap basemap...")
print("=" * 60)

# Determine orthomosaic paths - use stats if available, otherwise find files directly
if 'ortho_no_gcps_path' not in locals():
    if 'stats_no_gcps' in locals() and 'ortho_path' in stats_no_gcps:
        ortho_no_gcps_path = Path(stats_no_gcps['ortho_path'])
    else:
        ortho_output_dir = output_dir / "orthomosaics"
        ortho_no_gcps_path = ortho_output_dir / "orthomosaic_no_gcps.tif"
        if not ortho_no_gcps_path.exists():
            raise FileNotFoundError(f"Orthomosaic (no GCPs) not found at: {ortho_no_gcps_path.absolute()}")

if 'ortho_with_gcps_path' not in locals():
    if 'stats_with_gcps' in locals() and 'ortho_path' in stats_with_gcps:
        ortho_with_gcps_path = Path(stats_with_gcps['ortho_path'])
    else:
        ortho_output_dir = output_dir / "orthomosaics"
        ortho_with_gcps_path = ortho_output_dir / "orthomosaic_with_gcps.tif"
        if not ortho_with_gcps_path.exists():
            raise FileNotFoundError(f"Orthomosaic (with GCPs) not found at: {ortho_with_gcps_path.absolute()}")

# Compare without GCPs
print("\nComparing orthomosaic (without GCPs) to OpenStreetMap basemap...")
metrics_no_gcps_osm = compare_orthomosaic_to_basemap(
    ortho_path=ortho_no_gcps_path,
    basemap_path=Path(basemap_osm_path),
    output_dir=comparison_dir
)

# Compare with GCPs
print("\nComparing orthomosaic (with GCPs) to OpenStreetMap basemap...")
metrics_with_gcps_osm = compare_orthomosaic_to_basemap(
    ortho_path=ortho_with_gcps_path,
    basemap_path=Path(basemap_osm_path),
    output_dir=comparison_dir
)

print("\n✓ OpenStreetMap comparison complete!")

# Save metrics to JSON files for later use
if 'json' not in locals():
    import json
if 'convert_to_json_serializable' not in locals():
    from qualicum_beach_gcp_analysis.report_generator import convert_to_json_serializable

if 'metrics_dir' not in locals():
    metrics_dir = comparison_dir / "metrics"
    metrics_dir.mkdir(parents=True, exist_ok=True)

# Save OpenStreetMap metrics
metrics_no_gcps_osm_serializable = convert_to_json_serializable(metrics_no_gcps_osm)
metrics_with_gcps_osm_serializable = convert_to_json_serializable(metrics_with_gcps_osm)

with open(metrics_dir / "metrics_no_gcps_osm.json", 'w') as f:
    json.dump(metrics_no_gcps_osm_serializable, f, indent=2)
with open(metrics_dir / "metrics_with_gcps_osm.json", 'w') as f:
    json.dump(metrics_with_gcps_osm_serializable, f, indent=2)

print(f"✓ Metrics saved to: {metrics_dir}")


2025-12-02 15:03:15,492 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Comparing orthomosaic orthomosaic_no_gcps.tif to basemap qualicum_beach_basemap_osm.tif


Comparing orthomosaics to OpenStreetMap basemap...

Comparing orthomosaic (without GCPs) to OpenStreetMap basemap...


2025-12-02 15:03:30,149 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Saved reprojected raster to: outputs/comparisons/reprojected_orthomosaic_no_gcps.tif
2025-12-02 15:03:30,296 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Feature matching (sift) shift (-24.2, 83.0) too large, rejecting
2025-12-02 15:03:30,316 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Feature matching (orb) shift (54.1, 46.8) too large, rejecting
2025-12-02 15:03:30,317 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Phase correlation failed: local variable 'phase_cross_correlation' referenced before assignment
2025-12-02 15:03:30,321 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Template matching shift (51.0, -87.0) too large, rejecting
2025-12-02 15:03:30,325 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Comparison complete. Overall RMSE: 9.833849682430001
2025-12-02 15:03:30,325 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Comparing orth


Comparing orthomosaic (with GCPs) to OpenStreetMap basemap...


2025-12-02 15:03:45,616 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Saved reprojected raster to: outputs/comparisons/reprojected_orthomosaic_with_gcps.tif
2025-12-02 15:03:45,785 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Feature matching (sift) shift (-12.8, 54.2) too large, rejecting
2025-12-02 15:03:45,807 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Feature matching (orb) shift (-38.5, 24.4) too large, rejecting
2025-12-02 15:03:45,808 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Phase correlation failed: local variable 'phase_cross_correlation' referenced before assignment
2025-12-02 15:03:45,812 - qualicum_beach_gcp_analysis.quality_metrics - WARNING - Template matching shift (51.0, -87.0) too large, rejecting
2025-12-02 15:03:45,815 - qualicum_beach_gcp_analysis.quality_metrics - INFO - Comparison complete. Overall RMSE: 9.816594379223714



✓ OpenStreetMap comparison complete!
✓ Metrics saved to: outputs/comparisons/metrics


## Step 8: Generate Quality Reports


In [12]:
# Generate report for ESRI comparison
# Ensure imports and variables are defined
if 'Path' not in locals():
    from pathlib import Path

if 'generate_comparison_report' not in locals():
    from qualicum_beach_gcp_analysis import (
        generate_comparison_report, 
        generate_markdown_report,
        generate_latex_report,
        create_error_visualization,
        create_seamline_visualization,
        create_comparison_side_by_side,
        create_metrics_summary_plot
    )
    
if 'numpy' not in locals():
    import numpy as np
if 'rasterio' not in locals():
    import rasterio
if 'json' not in locals():
    import json

if 'output_dir' not in locals():
    output_dir = Path("outputs")
if 'comparison_dir' not in locals():
    comparison_dir = output_dir / "comparisons"

# Load metrics from Step 7 if available, otherwise check for saved files
if 'metrics_no_gcps_esri' not in locals() or 'metrics_with_gcps_esri' not in locals():
    # Try to load from saved JSON files
    metrics_dir = comparison_dir / "metrics"
    metrics_file_no_gcps = metrics_dir / "metrics_no_gcps_esri.json"
    metrics_file_with_gcps = metrics_dir / "metrics_with_gcps_esri.json"
    
    if metrics_file_no_gcps.exists() and metrics_file_with_gcps.exists():
        print(f"Loading saved metrics from: {metrics_dir}")
        with open(metrics_file_no_gcps, 'r') as f:
            metrics_no_gcps_esri = json.load(f)
        with open(metrics_file_with_gcps, 'r') as f:
            metrics_with_gcps_esri = json.load(f)
        print("✓ Loaded saved ESRI comparison metrics")
    else:
        raise NameError(
            f"metrics_no_gcps_esri and metrics_with_gcps_esri must be defined. "
            f"Please run Step 7 first, or ensure saved metrics exist at:\n"
            f"  {metrics_file_no_gcps}\n"
            f"  {metrics_file_with_gcps}"
        )

print("=" * 60)
print("Generating quality reports...")
print("=" * 60)

# ESRI report
report_json_esri = output_dir / "quality_report_esri.json"
report_md_esri = output_dir / "quality_report_esri.md"

generate_comparison_report(
    metrics_with_gcps=metrics_with_gcps_esri,
    metrics_without_gcps=metrics_no_gcps_esri,
    output_path=report_json_esri,
    basemap_source="ESRI World Imagery"
)

generate_markdown_report(
    json_report_path=report_json_esri,
    output_path=report_md_esri
)

print(f"\n✓ ESRI report saved:")
print(f"  JSON: {report_json_esri}")
print(f"  Markdown: {report_md_esri}")

# Ensure orthomosaic paths are defined
if 'ortho_no_gcps_path' not in locals():
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_no_gcps_path = ortho_output_dir / "orthomosaic_no_gcps.tif"
    if not ortho_no_gcps_path.exists():
        raise FileNotFoundError(f"Orthomosaic (no GCPs) not found at: {ortho_no_gcps_path.absolute()}")
if 'ortho_with_gcps_path' not in locals():
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_with_gcps_path = ortho_output_dir / "orthomosaic_with_gcps.tif"
    if not ortho_with_gcps_path.exists():
        raise FileNotFoundError(f"Orthomosaic (with GCPs) not found at: {ortho_with_gcps_path.absolute()}")
if 'basemap_esri_path' not in locals():
    basemap_esri_path = str(output_dir / "qualicum_beach_basemap_esri.tif")

# Generate visualizations for ESRI comparison
print("\nGenerating visualizations...")
vis_dir = output_dir / "visualizations" / "esri"
vis_dir.mkdir(parents=True, exist_ok=True)

# Load orthomosaics and reference for visualization
print("  Loading orthomosaics and reference basemap...")
with rasterio.open(ortho_no_gcps_path) as src:
    ortho_no_gcps = src.read(1)  # First band
with rasterio.open(ortho_with_gcps_path) as src:
    ortho_with_gcps = src.read(1)  # First band
with rasterio.open(basemap_esri_path) as src:
    reference_esri = src.read(1)  # First band

# Create visualizations
print("  Creating comparison visualizations...")
create_comparison_side_by_side(
    ortho_no_gcps, ortho_with_gcps, reference_esri,
    vis_dir / "comparison_side_by_side.png",
    title="ESRI Basemap Comparison"
)

create_metrics_summary_plot(
    metrics_no_gcps_esri, metrics_with_gcps_esri,
    vis_dir / "metrics_summary.png",
    title="ESRI Basemap Quality Metrics"
)

create_seamline_visualization(
    ortho_no_gcps,
    vis_dir / "seamlines_no_gcps.png",
    title="Seamlines - Without GCPs"
)

create_seamline_visualization(
    ortho_with_gcps,
    vis_dir / "seamlines_with_gcps.png",
    title="Seamlines - With GCPs"
)

create_error_visualization(
    ortho_no_gcps, reference_esri,
    vis_dir / "error_no_gcps.png",
    title="Error Map - Without GCPs"
)

create_error_visualization(
    ortho_with_gcps, reference_esri,
    vis_dir / "error_with_gcps.png",
    title="Error Map - With GCPs"
)

print(f"✓ Visualizations saved to: {vis_dir}")


# OpenStreetMap report
# Load metrics from Step 7 if available, otherwise check for saved files
if 'metrics_no_gcps_osm' not in locals() or 'metrics_with_gcps_osm' not in locals():
    # Try to load from saved JSON files
    if 'metrics_dir' not in locals():
        metrics_dir = comparison_dir / "metrics"
    metrics_file_no_gcps = metrics_dir / "metrics_no_gcps_osm.json"
    metrics_file_with_gcps = metrics_dir / "metrics_with_gcps_osm.json"
    
    if metrics_file_no_gcps.exists() and metrics_file_with_gcps.exists():
        print(f"Loading saved metrics from: {metrics_dir}")
        if 'json' not in locals():
            import json
        with open(metrics_file_no_gcps, 'r') as f:
            metrics_no_gcps_osm = json.load(f)
        with open(metrics_file_with_gcps, 'r') as f:
            metrics_with_gcps_osm = json.load(f)
        print("✓ Loaded saved OpenStreetMap comparison metrics")
    else:
        raise NameError(
            f"metrics_no_gcps_osm and metrics_with_gcps_osm must be defined. "
            f"Please run Step 7 first, or ensure saved metrics exist at:\n"
            f"  {metrics_file_no_gcps}\n"
            f"  {metrics_file_with_gcps}"
        )

report_json_osm = output_dir / "quality_report_osm.json"
report_md_osm = output_dir / "quality_report_osm.md"

generate_comparison_report(
    metrics_with_gcps=metrics_with_gcps_osm,
    metrics_without_gcps=metrics_no_gcps_osm,
    output_path=report_json_osm,
    basemap_source="OpenStreetMap"
)

generate_markdown_report(
    json_report_path=report_json_osm,
    output_path=report_md_osm
)

print(f"\n✓ OpenStreetMap report saved:")
print(f"  JSON: {report_json_osm}")
print(f"  Markdown: {report_md_osm}")

# Generate visualizations for OpenStreetMap comparison
print("\nGenerating visualizations for OpenStreetMap...")
vis_dir_osm = output_dir / "visualizations" / "osm"
vis_dir_osm.mkdir(parents=True, exist_ok=True)

# Ensure basemap path is defined
if 'basemap_osm_path' not in locals():
    basemap_osm_path = str(output_dir / "qualicum_beach_basemap_osm.tif")

# Load reference basemap for visualization
print("  Loading reference basemap...")
with rasterio.open(basemap_osm_path) as src:
    reference_osm = src.read(1)  # First band

# Reuse orthomosaics already loaded (or load if not available)
if 'ortho_no_gcps' not in locals():
    with rasterio.open(ortho_no_gcps_path) as src:
        ortho_no_gcps = src.read(1)
if 'ortho_with_gcps' not in locals():
    with rasterio.open(ortho_with_gcps_path) as src:
        ortho_with_gcps = src.read(1)

# Create visualizations
print("  Creating comparison visualizations...")
create_comparison_side_by_side(
    ortho_no_gcps, ortho_with_gcps, reference_osm,
    vis_dir_osm / "comparison_side_by_side.png",
    title="OpenStreetMap Basemap Comparison"
)

create_metrics_summary_plot(
    metrics_no_gcps_osm, metrics_with_gcps_osm,
    vis_dir_osm / "metrics_summary.png",
    title="OpenStreetMap Basemap Quality Metrics"
)

create_seamline_visualization(
    ortho_no_gcps,
    vis_dir_osm / "seamlines_no_gcps.png",
    title="Seamlines - Without GCPs"
)

create_seamline_visualization(
    ortho_with_gcps,
    vis_dir_osm / "seamlines_with_gcps.png",
    title="Seamlines - With GCPs"
)

create_error_visualization(
    ortho_no_gcps, reference_osm,
    vis_dir_osm / "error_no_gcps.png",
    title="Error Map - Without GCPs"
)

create_error_visualization(
    ortho_with_gcps, reference_osm,
    vis_dir_osm / "error_with_gcps.png",
    title="Error Map - With GCPs"
)

print(f"✓ Visualizations saved to: {vis_dir_osm}")

# Generate comprehensive LaTeX/PDF report with both ESRI and OSM
# Check for shifted metrics (from Step 7.5) and GCP-aligned metrics (from Step 7.6)
metrics_dir = comparison_dir / "metrics"
shifted_metrics_no_gcps_path = metrics_dir / "metrics_shifted_no_gcps_esri.json"
shifted_metrics_with_gcps_path = metrics_dir / "metrics_shifted_with_gcps_esri.json"
gcp_aligned_metrics_no_gcps_path = metrics_dir / "metrics_gcp_aligned_no_gcps_esri.json"
gcp_aligned_metrics_with_gcps_path = metrics_dir / "metrics_gcp_aligned_with_gcps_esri.json"

print("\n" + "=" * 60)
print("Generating comprehensive LaTeX/PDF report (ESRI + OSM)...")
print("=" * 60)

report_latex_final = output_dir / "quality_report_final"
latex_result_final = generate_latex_report(
    json_report_path=report_json_esri,
    output_path=report_latex_final,
    visualization_dir=vis_dir,
    json_report_path_osm=report_json_osm,
    visualization_dir_osm=vis_dir_osm,
    shifted_metrics_no_gcps_path=shifted_metrics_no_gcps_path if shifted_metrics_no_gcps_path.exists() else None,
    shifted_metrics_with_gcps_path=shifted_metrics_with_gcps_path if shifted_metrics_with_gcps_path.exists() else None,
    gcp_aligned_metrics_no_gcps_path=gcp_aligned_metrics_no_gcps_path if gcp_aligned_metrics_no_gcps_path.exists() else None,
    gcp_aligned_metrics_with_gcps_path=gcp_aligned_metrics_with_gcps_path if gcp_aligned_metrics_with_gcps_path.exists() else None
)

if latex_result_final.suffix == '.pdf':
    print(f"\n✓ PDF report generated: {latex_result_final}")
else:
    print(f"\n✓ LaTeX file generated: {latex_result_final}")
    print("  (Install LaTeX and run: pdflatex quality_report_final.tex to generate PDF)")



2025-12-02 15:03:45,828 - qualicum_beach_gcp_analysis.report_generator - INFO - Saved comparison report to: outputs/quality_report_esri.json
2025-12-02 15:03:45,829 - qualicum_beach_gcp_analysis.report_generator - INFO - Saved Markdown report to: outputs/quality_report_esri.md


Generating quality reports...

✓ ESRI report saved:
  JSON: outputs/quality_report_esri.json
  Markdown: outputs/quality_report_esri.md

Generating visualizations...
  Loading orthomosaics and reference basemap...
  Creating comparison visualizations...


NameError: name 'create_comparison_side_by_side' is not defined

## Step 9: Display Report Summary


In [ ]:
# Display summary from ESRI report
# Ensure imports and variables are defined
if 'Path' not in locals():
    from pathlib import Path
if 'json' not in locals():
    import json

if 'output_dir' not in locals():
    output_dir = Path("outputs")

# Define report paths
report_json_esri = output_dir / "quality_report_esri.json"
report_json_osm = output_dir / "quality_report_osm.json"
report_md_esri = output_dir / "quality_report_esri.md"
report_md_osm = output_dir / "quality_report_osm.md"

print("=" * 60)
print("QUALITY COMPARISON SUMMARY (ESRI World Imagery)")
print("=" * 60)

with open(report_json_esri, 'r') as f:
    report_esri = json.load(f)

comparison = report_esri.get('comparison', {})

if comparison.get('rmse_improvement'):
    rmse = comparison['rmse_improvement']
    print(f"\nRMSE Improvement: {rmse['percentage']:+.2f}%")
    print(f"  Without GCPs: {rmse['without_gcps']:.4f}")
    print(f"  With GCPs:    {rmse['with_gcps']:.4f}")

if comparison.get('mae_improvement'):
    mae = comparison['mae_improvement']
    print(f"\nMAE Improvement: {mae['percentage']:+.2f}%")
    print(f"  Without GCPs: {mae['without_gcps']:.4f}")
    print(f"  With GCPs:    {mae['with_gcps']:.4f}")

if comparison.get('similarity_improvement'):
    sim = comparison['similarity_improvement']
    print(f"\nSimilarity Improvement: {sim['percentage']:+.2f}%")
    print(f"  Without GCPs: {sim['without_gcps']:.4f}")
    print(f"  With GCPs:    {sim['with_gcps']:.4f}")

if comparison.get('seamline_reduction'):
    seam = comparison['seamline_reduction']
    print(f"\nSeamline Reduction: {seam['percentage']:+.2f}%")
    print(f"  Without GCPs: {seam['without_gcps']:.2f}%")
    print(f"  With GCPs:    {seam['with_gcps']:.2f}%")

print("\n" + "=" * 60)
print(f"Full reports available at:")
print(f"  {report_md_esri}")
print(f"  {report_md_osm}")
print("=" * 60)
